### The alternant decoder BMS

In [1]:
import os 
os.chdir('C:\\Users\\usuario\\ownCloud\\public_html\\CC2')
# Current extension patch to CC
from CC_x import *

def alternant_decoder(y,C):
    K = K_(C)
    if K_(y) != K:
        if K.is_sub_domain(K_(y)):
            if isinstance(y,list): y = vector(K,y)
            elif isinstance(y,Vector_type):
                y = y*(1>>K)
            else:
                return "AD: Argument is not a vector"
        else:
            return "AD: Fields of argument and code are different"
    if isinstance(y,list): y = vector(K,y)
    if not isinstance(y,Vector_type):
        return "AD: Argument is not a vector"
    
    h = h_(C)
    if len(y) != len(h):
        return "AD: Vector argument has wrong length"
    r = r_(C); a = a_(C); b = b_(C)
    H = H_(C); K1 = K_(H)
    y1 = vector([t for t in y])
    s = y1*H.transpose()
    #print('s:',s)
    if is_zero(s): 
        print("AD: Input is a code vector")
        return y1
    [_,z] = polynomial_ring(K1,'z','K[z]')
    S = hohner(s,z).reverse()
    if degree(S)< r//2 or trailing_degree(S)>= r//2:
        return "AD: Non-decodable vector: extraneous syndrome"
    (L,E)=sugiyama(z**r,S,r//2)
    M = zero_positions(L,b)
    
    if K == Zn(2):
        for j in range(len(M)):
            y1[M[j]] = pull(flip(y1,M[j]),K)
            if not belongs(y1[M[j]],K):
                return "AD: error value not in base field"
        return y1
    
    if len(M)<degree(L):
        return "AD: non-decodable vector: too few locator roots"
    L = der(L)
    err = []
    for m in M:
        #show(m)
        x = (a[m]*evaluate(E,b[m]))/(h[m]*evaluate(L,b[m]))
        x = pull(x,K)
        if not belongs(x,K):
            return "AD: Non-decodable vector: Forney value not in base field"
            show(-x)
        err += [-x]
        y1[m] = y1[m]+x
    #show('y1:',y1)
    if is_zero(y1*H.transpose()):
        print("AD: Successful decoding with error table:\n",M,'\n',vector(err))
        return y1
    else: return "AD: Decoder error: output vector has non-zero syndrome"
# alias
BMS = AD = alternant_decoder